# 3D Visualization of Earth and Satellite Orbits

This notebook provides a 3D visualization of Earth and the growing number of satellites in orbit. It aims to highlight the scale of the satellite population and introduces the concept of using Quantum Computing for orbit optimization.

## 1. Installation

Run the following cell to install the necessary libraries. If you have them already installed, you can skip this step.

In [1]:
%pip install plotly numpy


[notice] A new release of pip is available: 24.1.2 -> 25.3
[notice] To update, run: python3 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


## 2. Creating the 3D Model of Earth

First, we'll create a 3D model of the Earth using Plotly. We'll represent the Earth as a blue sphere. For a more realistic representation, one could even map a texture of the Earth's surface onto the sphere, but for the purpose of this visualization, a simple sphere will suffice to provide the necessary context for the satellite orbits.

In [2]:
import plotly.graph_objects as go
import numpy as np

# Create the Earth sphere
earth_radius = 6371  # Earth radius in km
theta = np.linspace(0, 2*np.pi, 100)
phi = np.linspace(0, np.pi, 100)
x_earth = earth_radius * np.outer(np.cos(theta), np.sin(phi))
y_earth = earth_radius * np.outer(np.sin(theta), np.sin(phi))
z_earth = earth_radius * np.outer(np.ones(100), np.cos(phi))

earth = go.Surface(
    x=x_earth,
    y=y_earth,
    z=z_earth,
    colorscale=[[0, 'blue'], [1, 'blue']],
    showscale=False,
    name='Earth'
)

## 3. Simulating Satellite Orbits

Next, we'll simulate the positions of 100,000 satellites. To keep the simulation manageable, we'll generate random circular orbits at different altitudes and inclinations. In reality, satellite orbits are more complex (e.g., elliptical), but this simulation will effectively demonstrate the density of satellites around our planet.

In [3]:
def generate_satellite_orbits(num_satellites, min_altitude, max_altitude):
    """
    Generates random satellite positions in orbit around the Earth.
    
    Args:
        num_satellites (int): The number of satellites to generate.
        min_altitude (float): The minimum orbital altitude in km.
        max_altitude (float): The maximum orbital altitude in km.
        
    Returns:
        A tuple of (x, y, z) coordinates for the satellites.
    """
    # Generate random altitudes for each satellite
    altitudes = np.random.uniform(min_altitude, max_altitude, num_satellites)
    radii = earth_radius + altitudes
    
    # Generate random orbital parameters
    inclinations = np.random.uniform(0, np.pi, num_satellites)
    longitudes = np.random.uniform(0, 2 * np.pi, num_satellites)
    
    # Generate random positions in orbit
    thetas = np.random.uniform(0, 2 * np.pi, num_satellites)
    
    # Convert spherical to Cartesian coordinates
    x = radii * np.sin(inclinations) * np.cos(longitudes)
    y = radii * np.sin(inclinations) * np.sin(longitudes)
    z = radii * np.cos(inclinations)
    
    return x, y, z

# Generate 100,000 satellites in Low Earth Orbit (LEO)
num_satellites = 100000
min_altitude = 300  # LEO starts at ~160 km, but is densest from 300km
max_altitude = 2000 # LEO ends at 2000 km

x_sats, y_sats, z_sats = generate_satellite_orbits(num_satellites, min_altitude, max_altitude)

satellites = go.Scatter3d(
    x=x_sats,
    y=y_sats,
    z=z_sats,
    mode='markers',
    marker=dict(
        size=1.5,
        color='red',
        opacity=0.8
    ),
    name='Satellites'
)

## 4. Interactive 3D Visualization

Now, let's combine the Earth model and the satellite data into a single interactive 3D plot. You can rotate, pan, and zoom to explore the visualization from different angles. This will provide a compelling view of the density of satellites in Low Earth Orbit.

In [4]:
fig = go.Figure(data=[earth, satellites])

fig.update_layout(
    title_text='Density of Satellites in Low Earth Orbit',
    scene=dict(
        xaxis_title='X (km)',
        yaxis_title='Y (km)',
        zaxis_title='Z (km)',
        aspectmode='data' # This ensures the sphere is not distorted
    ),
    margin=dict(r=20, l=10, b=10, t=40)
)

fig.show()

## 5. Quantum Computing for Orbit Optimization

The visualization above illustrates the congestion in Earth's orbit. Managing this ever-growing number of satellites to prevent collisions and ensure efficient coverage is a massive optimization problem. This is where Quantum Computing could offer a significant advantage.

Classical computers struggle with the complexity of such large-scale optimization problems, as the number of possible configurations grows exponentially with the number of satellites. Quantum computers, on the other hand, are designed to handle such complex problems by leveraging the principles of quantum mechanics, like superposition and entanglement.

### Quadratic Unconstrained Binary Optimization (QUBO)

One common approach to solving optimization problems on a quantum computer is to formulate them as a **Quadratic Unconstrained Binary Optimization (QUBO)** problem. A QUBO problem is defined by an objective function of the form:

$$ f(x) = \sum_{i} Q_{ii}x_i + \sum_{i<j} Q_{ij}x_i x_j $$

where $x_i$ are binary variables (0 or 1) and $Q$ is a matrix of coefficients. The goal is to find the assignment of binary variables that minimizes this function.

For our satellite problem, we could define the binary variables to represent decisions about satellite placement or trajectory adjustments. For example, a variable could represent whether a satellite should be in a particular orbital slot at a given time. The $Q$ matrix would encode the costs and benefits of these decisions, such as:

- **Collision Risk:** A high cost for two satellites being in close proximity.
- **Coverage:** A benefit for placing satellites in a way that provides optimal ground coverage.
- **Fuel Efficiency:** A cost for making orbital maneuvers.

By minimizing the QUBO function, we can find an optimal configuration of the satellite constellation that balances these competing objectives.

### Conceptual Example with Qiskit

While a full implementation is beyond the scope of this notebook, the following code provides a conceptual example of how you might approach a simplified version of this problem using **Qiskit**, an open-source quantum computing software development kit.

Here, we define a small QUBO problem and use a classical solver from Qiskit to find the optimal solution. In a real-world scenario, you would run this on a quantum computer or a quantum simulator for larger and more complex problems.

In [5]:
%pip install qiskit qiskit-optimization

from qiskit_optimization.applications import Maxcut
from qiskit_optimization.converters import QuadraticProgramToQubo
from qiskit_optimization.algorithms import MinimumEigenOptimizer
from qiskit.algorithms.minimum_eigensolvers import NumPyMinimumEigensolver
import numpy as np

# --- 1. Define a simplified problem ---
# Let's model a toy problem with 4 orbital 'slots' (nodes in a graph).
# The weights between nodes represent the 'cost' of placing satellites in both slots
# (e.g., collision risk). We want to partition the satellites into two sets of orbits
# to minimize this cost.

num_slots = 4
adj_matrix = np.array([
    [0, 1, 1, 0], # Slot 0 has a conflict with 1 and 2
    [1, 0, 1, 1], # Slot 1 has a conflict with 0, 2 and 3
    [1, 1, 0, 1], # Slot 2 has a conflict with 0, 1 and 3
    [0, 1, 1, 0]  # Slot 3 has a conflict with 1 and 2
])

# This is a Max-Cut problem, which is equivalent to a QUBO.
# We want to partition the graph to maximize the number of edges between the two sets.
max_cut = Maxcut(adj_matrix)
qp = max_cut.to_quadratic_program()

# --- 2. Convert to QUBO ---
qubo_converter = QuadraticProgramToQubo()
qubo = qubo_converter.convert(qp)

# --- 3. Solve the QUBO ---
# We use a classical solver here for simplicity.
# For a real quantum approach, you would use a quantum algorithm like QAOA or VQE.
numpy_solver = NumPyMinimumEigensolver()
optimizer = MinimumEigenOptimizer(numpy_solver)
result = optimizer.solve(qubo)

# --- 4. Interpret the results ---
print(f"Optimal solution: {result.x}")
print(f"This means we can partition the slots into two sets: ")
set_A = [i for i, x in enumerate(result.x) if x == 0]
set_B = [i for i, x in enumerate(result.x) if x == 1]
print(f"  Set A: {set_A}")
print(f"  Set B: {set_B}")
print("This partitioning minimizes the conflicts between the orbital slots.")


[notice] A new release of pip is available: 24.1.2 -> 25.3
[notice] To update, run: python3 -m pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


TypeError: type 'typing.TypeVar' is not an acceptable base type

## 6. Starlink Telemetry Integration with Real Data

Now let's integrate **real Starlink telemetry patterns** from the opendatabay.com dataset to augment our satellite visualization with performance metrics like signal quality, throughput, and packet loss.

In [ ]:
# Import the Starlink telemetry generator
import sys
sys.path.append('.')  # Add current directory to path

from starlink_telemetry import StarlinkTelemetryGenerator, print_telemetry_summary
import math

# Initialize telemetry generator with seed for reproducibility
telemetry_gen = StarlinkTelemetryGenerator(seed=42)

print("✓ Starlink Telemetry Generator loaded successfully!")
print("  Dataset schema: 13 columns from opendatabay.com")
print("  Metrics: QoE, throughput, signal loss, packet loss, weather conditions")

### Generate Sample Satellites with Telemetry

Let's create a smaller set of satellites (20 satellites) with realistic positions and augment them with Starlink telemetry data.

In [ ]:
# Generate realistic satellite positions for Starlink constellation
np.random.seed(42)
num_starlink_sats = 20
min_alt_starlink = 340  # Starlink altitude ~340-1200 km
max_alt_starlink = 1200

# Generate positions
altitudes = np.random.uniform(min_alt_starlink, max_alt_starlink, num_starlink_sats)
latitudes = np.random.uniform(-60, 60, num_starlink_sats)  # Starlink coverage ±60°
longitudes = np.random.uniform(-180, 180, num_starlink_sats)

# Create position dictionary for telemetry generation
starlink_positions = {}
for i in range(num_starlink_sats):
    sat_id = 50000 + i  # Fictional NORAD IDs
    starlink_positions[sat_id] = {
        'lat': latitudes[i],
        'lng': longitudes[i],
        'alt': altitudes[i]
    }

# Generate telemetry data for all satellites
augmented_starlink = telemetry_gen.augment_satellite_positions(starlink_positions)

print(f"Generated {num_starlink_sats} Starlink satellites with telemetry data")
print("\nSample satellite data:")
sample_id = list(augmented_starlink.keys())[0]
sample_data = augmented_starlink[sample_id]
print(f"  Satellite {sample_id}:")
print(f"    Position: ({sample_data['latitude']:.2f}°, {sample_data['longitude']:.2f}°) @ {sample_data['altitude_km']:.0f} km")
print(f"    Weather: {sample_data['weather']}")
print(f"    QoE Score: {sample_data['qoe_score']}/10")
print(f"    Download: {sample_data['download_throughput_mbps']:.1f} Mbps")
print(f"    Packet Loss: {sample_data['packet_loss_percent']:.2f}%")

### Next Steps and Further Reading

This notebook provides a starting point for your exploration. To delve deeper into this topic, you could:

- **Use more realistic satellite data:** You can find publicly available satellite data from sources like CelesTrak.
- **Model more complex orbits:** Extend the simulation to include elliptical orbits and other orbital parameters.
- **Explore different quantum algorithms:** Investigate algorithms like the Quantum Approximate Optimization Algorithm (QAOA) and the Variational Quantum Eigensolver (VQE) for solving QUBO problems.
- **Learn more about Qiskit:** The [Qiskit documentation](https.qiskit.org/documentation/) is an excellent resource for learning more about quantum computing and how to use the Qiskit library.